In [1]:
import os
import time
import torch
import torch as tc
import torch.nn as nn
import torch.nn.parallel
import torch.backends.cudnn as cudnn
import torch.optim as optim
import torch.utils.data
import torchvision.datasets as dset
import torchvision.transforms as transforms
import torchvision.utils as vutils
from torch.autograd import Variable
import matplotlib.pyplot as plt
%matplotlib inline
from PIL import Image
import numpy as np
import sys,os

In [2]:
import models
from models import weights_init

# Main code

In [3]:
#Libera as funcionalidades da biblioteca cudnn
cudnn.benchmark = True

use_gpu = torch.cuda.is_available()
#use_gpu = False
if use_gpu:
    print("You are using CUDA. If it is not what you want, manually set this as False!")

You are using CUDA. If it is not what you want, manually set this as False!


In [4]:
nc = 3
ngpu = 1
nz = 100
ngf = 64
ndf = 64
n_extra_d = 0
n_extra_g = 1 # Aqui a jogada é que o gerador deve ser mais poderoso q o detetive
imageSize = 64

In [5]:
!cd images && pwd


/home/gabriel/Redes Neurais/Projeto_Final_GANS/Tutorial_2/images


## Setando as transformações

In [6]:
!ls images/images2/

ls: cannot access 'images/images2/': No such file or directory


In [7]:
!ls dataset

anime-faces  min_anime-faces  teste


In [8]:
dataset = dset.ImageFolder(
    root='/home/gabriel/Redes Neurais/Projeto_Final_GANS/Tutorial_2/dataset/min_anime-faces',
    transform=transforms.Compose([
            transforms.Scale((imageSize, imageSize)),
            # transforms.CenterCrop(opt.imageSize),
            transforms.ToTensor(),
            #transforms.Normalize((0.5,0.5,0.5), (0.5,0.5,0.5)), # bring images to (-1,1)
        ])
)

## Setando o Dataloader

In [9]:
batch_size=64
num_workers = 4

In [10]:

dataloader = tc.utils.data.DataLoader(dataset, batch_size=64, shuffle=True, num_workers=1)
#126 classes

## Setando o modelo

### Modelo DCGAN

In [11]:
class _netD_1(nn.Module):
    def __init__(self, ngpu, nz, nc, ndf,  n_extra_layers_d):
        super(_netD_1, self).__init__()
        self.ngpu = ngpu
        main = nn.Sequential(
            # input is (nc) x 96 x 96
            nn.Conv2d(nc, ndf, 4, 2, 1, bias=False), # 5,3,1 for 96x96
            nn.LeakyReLU(0.2, inplace=True),
            # state size. (ndf) x 32 x 32
            nn.Conv2d(ndf, ndf * 2, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ndf * 2),
            nn.LeakyReLU(0.2, inplace=True),
            # state size. (ndf*2) x 16 x 16
            nn.Conv2d(ndf * 2, ndf * 4, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ndf * 4),
            nn.LeakyReLU(0.2, inplace=True),
            # state size. (ndf*4) x 8 x 8
            nn.Conv2d(ndf * 4, ndf * 8, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ndf * 8),
            nn.LeakyReLU(0.2, inplace=True),
            # state size. (ndf*8) x 4 x 4
        )

        # Extra layers
        for t in range(n_extra_layers_d):
            main.add_module('extra-layers-{0}.{1}.conv'.format(t, ndf * 8),
                            nn.Conv2d(ndf * 8, ndf * 8, 3, 1, 1, bias=False))
            main.add_module('extra-layers-{0}.{1}.batchnorm'.format(t, ndf * 8),
                            nn.BatchNorm2d(ndf * 8))
            main.add_module('extra-layers-{0}.{1}.relu'.format(t, ndf * 8),
                            nn.LeakyReLU(0.2, inplace=True))


        main.add_module('final_layers.conv', nn.Conv2d(ndf * 8, 1, 4, 1, 0, bias=False))
        main.add_module('final_layers.sigmoid', nn.Sigmoid())
        # state size. 1 x 1 x 1
        self.main = main

    def forward(self, input):
        gpu_ids = None
        if isinstance(input.data, torch.cuda.FloatTensor) and self.ngpu > 1:
            gpu_ids = range(self.ngpu)
        output = nn.parallel.data_parallel(self.main, input, gpu_ids)
        return output.view(-1, 1)


In [12]:
# DCGAN model, fully convolutional architecture
class _netG_1(nn.Module):
    def __init__(self, ngpu, nz, nc , ngf, n_extra_layers_g):
        super(_netG_1, self).__init__()
        self.ngpu = ngpu
        #self.nz = nz
        #self.nc = nc
        #self.ngf = ngf
        main = nn.Sequential(
            # input is Z, going into a convolution
            # state size. nz x 1 x 1
            nn.ConvTranspose2d(     nz, ngf * 8, 4, 1, 0, bias=False),
            nn.BatchNorm2d(ngf * 8),
            nn.LeakyReLU(0.2, inplace=True),
            # state size. (ngf*8) x 4 x 4
            nn.ConvTranspose2d(ngf * 8, ngf * 4, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ngf * 4),
            nn.LeakyReLU(0.2, inplace=True),
            # state size. (ngf*4) x 8 x 8
            nn.ConvTranspose2d(ngf * 4, ngf * 2, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ngf * 2),
            nn.LeakyReLU(0.2, inplace=True),
            # state size. (ngf*2) x 16 x 16
            nn.ConvTranspose2d(ngf * 2,     ngf, 4, 2, 1, bias=False),
            nn.BatchNorm2d(ngf),
            nn.LeakyReLU(0.2, inplace=True),
            # state size. (ngf) x 32 x 32
        )

        # Extra layers
        for t in range(n_extra_layers_g):
            main.add_module('extra-layers-{0}.{1}.conv'.format(t, ngf),
                            nn.Conv2d(ngf, ngf, 3, 1, 1, bias=False))
            main.add_module('extra-layers-{0}.{1}.batchnorm'.format(t, ngf),
                            nn.BatchNorm2d(ngf))
            main.add_module('extra-layers-{0}.{1}.relu'.format(t, ngf),
                            nn.LeakyReLU(0.2, inplace=True))

        main.add_module('final_layer.deconv', 
        	             nn.ConvTranspose2d(ngf, nc, 4, 2, 1, bias=False)) # 5,3,1 for 96x96
        main.add_module('final_layer.tanh', 
        	             nn.Tanh())
            # state size. (nc) x 96 x 96

        self.main = main


    def forward(self, input):
        gpu_ids = None
        if isinstance(input.data, torch.cuda.FloatTensor) and self.ngpu > 1:
            gpu_ids = range(self.ngpu)
        return nn.parallel.data_parallel(self.main, input, gpu_ids), 0

In [13]:
#netG = _netG_1(ngpu, nz, nc, ngf, n_extra_g)
netG_parallel = torch.nn.DataParallel(_netG_1(ngpu, nz, nc, ngf, n_extra_g))

In [14]:
#print(netG)
print(netG_parallel)

DataParallel (
  (module): _netG_1 (
    (main): Sequential (
      (0): ConvTranspose2d(100, 512, kernel_size=(4, 4), stride=(1, 1), bias=False)
      (1): BatchNorm2d(512, eps=1e-05, momentum=0.1, affine=True)
      (2): LeakyReLU (0.2, inplace)
      (3): ConvTranspose2d(512, 256, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
      (4): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True)
      (5): LeakyReLU (0.2, inplace)
      (6): ConvTranspose2d(256, 128, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
      (7): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=True)
      (8): LeakyReLU (0.2, inplace)
      (9): ConvTranspose2d(128, 64, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
      (10): BatchNorm2d(64, eps=1e-05, momentum=0.1, affine=True)
      (11): LeakyReLU (0.2, inplace)
      (extra-layers-0.64.conv): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (extra-layers-0.64.batchnorm):

In [15]:
#netD = _netD_1(ngpu, nz, nc, ndf, n_extra_d)

netD_parallel = torch.nn.DataParallel(_netD_1(ngpu, nz, nc, ndf, n_extra_d))

In [16]:
print(netD_parallel)
#print(netD)

DataParallel (
  (module): _netD_1 (
    (main): Sequential (
      (0): Conv2d(3, 64, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
      (1): LeakyReLU (0.2, inplace)
      (2): Conv2d(64, 128, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
      (3): BatchNorm2d(128, eps=1e-05, momentum=0.1, affine=True)
      (4): LeakyReLU (0.2, inplace)
      (5): Conv2d(128, 256, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
      (6): BatchNorm2d(256, eps=1e-05, momentum=0.1, affine=True)
      (7): LeakyReLU (0.2, inplace)
      (8): Conv2d(256, 512, kernel_size=(4, 4), stride=(2, 2), padding=(1, 1), bias=False)
      (9): BatchNorm2d(512, eps=1e-05, momentum=0.1, affine=True)
      (10): LeakyReLU (0.2, inplace)
      (final_layers.conv): Conv2d(512, 1, kernel_size=(4, 4), stride=(1, 1), bias=False)
      (final_layers.sigmoid): Sigmoid ()
    )
  )
)


# Carregando pesos pré-treinados

In [17]:
def weights_init(m):
    classname = m.__class__.__name__
    if classname.find('Conv') != -1:
        m.weight.data.normal_(0.0, 0.02)
    elif classname.find('BatchNorm') != -1:
        m.weight.data.normal_(1.0, 0.02)
        m.bias.data.fill_(0)


In [18]:
#Parece ser um inicializador de pesos hardcoded
#netG.apply(weights_init)
netG_parallel.apply(weights_init)
#netD.apply(weights_init)
netD_parallel.apply(weights_init)
print(())

()


load=False
if load:
    netD.load_state_dict(tc.load('path_d'))
    
    netG.load_state_dict(torch.load('path_G'))


### Parametros de treinamento

In [19]:
criterion = nn.BCELoss()
criterion_MSE = nn.MSELoss()


In [20]:

input = torch.FloatTensor(batch_size, 3, imageSize, imageSize)
print(input.size())
noise = torch.FloatTensor(batch_size, nz, 1, 1)
print(noise.size())

torch.Size([64, 3, 64, 64])
torch.Size([64, 100, 1, 1])


In [21]:
#parser.add_argument('--binary', action='store_true', help='z from bernoulli distribution, with prob=0.5')
binary=False
#Ele testa pergunta se vc quer que o seu Z venha da distribuição bernoulli
if binary:
    bernoulli_prob = torch.FloatTensor(batch_size, nz, 1, 1).fill_(0.5)
    fixed_noise = torch.bernoulli(bernoulli_prob)
else:
    fixed_noise = torch.FloatTensor(batch_size, nz, 1, 1).normal_(0, 1)


In [22]:
label = torch.FloatTensor(batch_size)
real_label = 1
fake_label = 0


### Broadcast para CUDA, se quiser

In [23]:
if use_gpu:
    #netD.cuda()
    #netG.cuda()
    netD_parallel.cuda()
    netG_parallel.cuda()
    criterion = criterion.cuda()
    criterion_MSE = criterion_MSE.cuda()
    input,label = input.cuda(), label.cuda()
    noise, fixed_noise = noise.cuda(), fixed_noise.cuda()

### Transformando tudo em variable

In [24]:

input = Variable(input)
label = Variable(label)
noise = Variable(noise)
fixed_noise = Variable(fixed_noise)


### Setando o optimizer

In [25]:
beta1, beta2 = 0.9,0.999
lr = 2.0e-4
#optimizerD = optim.Adam(netD.parameters(), lr = lr, betas = (beta1, beta2))
optimizerD = optim.Adam(netD_parallel.parameters(), lr = lr, betas = (beta1, beta2))

#optimizerG = optim.Adam(netG.parameters(), lr = lr, betas = (beta1, beta2))
optimizerG = optim.Adam(netG_parallel.parameters(), lr = lr, betas = (beta1, beta2))


### Criando o diretório vazio

In [26]:
outputDir = 'outputdir_parallel'

try:
    os.makedirs(outputDir)
except OSError as err:
    print("OS error: {0}".format(err))

OS error: [Errno 17] File exists: 'outputdir_parallel'


## Treinando !

In [27]:
print(type(input))
print(input.size())
print(label.size())

<class 'torch.autograd.variable.Variable'>
torch.Size([64, 3, 64, 64])
torch.Size([64])


In [33]:
for i, data in enumerate(dataloader, 0):
    if i>4:
        break
    start_iter = time.time()
    ############################
    # (1) Update D network: maximize log(D(x)) + log(1 - D(G(z)))
    ###########################

    # TRAIN WITH REAL DATA
    #--------------------
    netD_parallel.zero_grad()
    real_cpu, _ = data
    batch_size = real_cpu.size(0)
    input.data.resize_(real_cpu.size()).copy_(real_cpu)
    label.data.resize_(batch_size).fill_(real_label - d_labelSmooth) # use smooth label for discriminator

    output = netD_parallel(input)
    errD_real = criterion(output, label)
    D_x = output.data.mean()

/home/gabriel/anaconda3/envs/py35/lib/python3.5/site-packages/torch/nn/functional.py:767: UserWarning: Using a target size (torch.Size([64])) that is different to the input size (torch.Size([64, 1])) is deprecated. Please ensure they have the same size.
  "Please ensure they have the same size.".format(target.size(), input.size()))


In [28]:
def train_both_networks(num_epochs, dataloader, netD, netG, d_labelSmooth, outputDir, model_option =1,binary = False):
    use_gpu = tc.cuda.is_available()

    for epoch in range(num_epochs):
        for i, data in enumerate(dataloader, 0):
            start_iter = time.time()
            ############################
            # (1) Update D network: maximize log(D(x)) + log(1 - D(G(z)))
            ###########################
            
            # TRAIN WITH REAL DATA
            #--------------------
            netD.zero_grad()
            real_cpu, _ = data
            batch_size = real_cpu.size(0)
            input.data.resize_(real_cpu.size()).copy_(real_cpu)
            label.data.resize_(batch_size).fill_(real_label - d_labelSmooth) # use smooth label for discriminator

            output = netD(input)
            errD_real = criterion(output, label)
            errD_real.backward()
            D_x = output.data.mean()
            #------------------
            # TRAIN WITH FAKE DATA
            #------------------
            
            noise.data.resize_(batch_size, nz, 1, 1)
            if binary:
                bernoulli_prob.resize_(noise.data.size())
                noise.data.copy_(2*(torch.bernoulli(bernoulli_prob)-0.5))
            else:
                noise.data.normal_(0, 1)
            fake,z_prediction = netG(noise)
            label.data.fill_(fake_label)
            output = netD(fake.detach()) # add ".detach()" to avoid backprop through G
            errD_fake = criterion(output, label)
            errD_fake.backward() # gradients for fake/real will be accumulated
            D_G_z1 = output.data.mean()
            errD = errD_real + errD_fake
            optimizerD.step() # .step() can be called once the gradients are computed

            ############################
            # (2) Update G network: maximize log(D(G(z)))
            ###########################
            netG.zero_grad()
            # Next line fill label with 1's
            label.data.fill_(real_label) # fake labels are real for generator cost
            # 'fake' is the false images created by the "FAKER"
            output = netD(fake)
            errG = criterion(output, label)
            errG.backward(retain_variables=True) # True if backward through the graph for the second time
            if model_option == 2: # with z predictor
                errG_z = criterion_MSE(z_prediction, noise)
                errG_z.backward()
            D_G_z2 = output.data.mean()
            optimizerG.step()

            end_iter = time.time()
            print('[%d/%d][%d/%d] Loss_D: %.4f Loss_G: %.4f D(x): %.4f D(G(z)): %.4f / %.4f Elapsed %.2f s'
                  % (epoch, num_epochs, i, len(dataloader),
                     errD.data[0], errG.data[0], D_x, D_G_z1, D_G_z2, end_iter-start_iter))
            if i % 100 == 0:
                # the first 64 samples from the mini-batch are saved.
                vutils.save_image(real_cpu[0:64,:,:,:],
                        '%s/real_samples.png' % outputDir, nrow=8)
                fake,_ = netG(fixed_noise)
                vutils.save_image(fake.data[0:64,:,:,:],
                        '%s/fake_samples_epoch_%03d.png' % (outputDir, epoch), nrow=8)
        if epoch % 1 == 0:
            # do checkpointing
            torch.save(netG.state_dict(), '%s/netG_epoch_%d.pth' % (outputDir, epoch))
            torch.save(netD.state_dict(), '%s/netD_epoch_%d.pth' % (outputDir, epoch))

In [29]:
num_epochs = 100
d_labelSmooth = 0.2

train_both_networks(num_epochs, dataloader, netD_parallel,netG_parallel,d_labelSmooth, outputDir)

/home/gabriel/anaconda3/envs/py35/lib/python3.5/site-packages/torch/nn/functional.py:767: UserWarning: Using a target size (torch.Size([64])) that is different to the input size (torch.Size([64, 1])) is deprecated. Please ensure they have the same size.
  "Please ensure they have the same size.".format(target.size(), input.size()))
/home/gabriel/anaconda3/envs/py35/lib/python3.5/site-packages/torch/autograd/__init__.py:92: UserWarning: retain_variables option is deprecated and will be removed in 0.3. Use retain_graph instead.
  warnings.warn("retain_variables option is deprecated and will be removed in 0.3. "


[0/100][0/472] Loss_D: 1.9173 Loss_G: 4.7895 D(x): 0.3830 D(G(z)): 0.5337 / 0.0111 Elapsed 0.59 s
[0/100][1/472] Loss_D: 1.2354 Loss_G: 6.1327 D(x): 0.9514 D(G(z)): 0.3068 / 0.0031 Elapsed 0.06 s
[0/100][2/472] Loss_D: 0.8155 Loss_G: 7.0067 D(x): 0.9075 D(G(z)): 0.0802 / 0.0013 Elapsed 0.06 s
[0/100][3/472] Loss_D: 0.7080 Loss_G: 6.9739 D(x): 0.7305 D(G(z)): 0.0298 / 0.0015 Elapsed 0.06 s
[0/100][4/472] Loss_D: 0.8107 Loss_G: 5.8254 D(x): 0.5900 D(G(z)): 0.0362 / 0.0048 Elapsed 0.06 s
[0/100][5/472] Loss_D: 0.8067 Loss_G: 4.9768 D(x): 0.7065 D(G(z)): 0.0959 / 0.0103 Elapsed 0.06 s
[0/100][6/472] Loss_D: 0.8633 Loss_G: 5.3872 D(x): 0.8564 D(G(z)): 0.1714 / 0.0073 Elapsed 0.06 s
[0/100][7/472] Loss_D: 0.8169 Loss_G: 6.4374 D(x): 0.8786 D(G(z)): 0.1760 / 0.0026 Elapsed 0.06 s
[0/100][8/472] Loss_D: 0.7498 Loss_G: 7.6252 D(x): 0.7529 D(G(z)): 0.0549 / 0.0008 Elapsed 0.06 s
[0/100][9/472] Loss_D: 0.7381 Loss_G: 8.0523 D(x): 0.7006 D(G(z)): 0.0262 / 0.0007 Elapsed 0.06 s
[0/100][10/472] Loss

[0/100][85/472] Loss_D: 0.5464 Loss_G: 8.5713 D(x): 0.8131 D(G(z)): 0.0020 / 0.0002 Elapsed 0.06 s
[0/100][86/472] Loss_D: 0.6760 Loss_G: 6.7868 D(x): 0.6319 D(G(z)): 0.0024 / 0.0012 Elapsed 0.06 s
[0/100][87/472] Loss_D: 0.6430 Loss_G: 6.1328 D(x): 0.9073 D(G(z)): 0.0146 / 0.0023 Elapsed 0.06 s
[0/100][88/472] Loss_D: 0.6830 Loss_G: 6.9767 D(x): 0.8831 D(G(z)): 0.0322 / 0.0010 Elapsed 0.06 s
[0/100][89/472] Loss_D: 0.6116 Loss_G: 8.1103 D(x): 0.8146 D(G(z)): 0.0132 / 0.0003 Elapsed 0.06 s
[0/100][90/472] Loss_D: 0.6364 Loss_G: 8.2270 D(x): 0.7290 D(G(z)): 0.0054 / 0.0003 Elapsed 0.06 s
[0/100][91/472] Loss_D: 0.7213 Loss_G: 6.4014 D(x): 0.5978 D(G(z)): 0.0064 / 0.0018 Elapsed 0.06 s
[0/100][92/472] Loss_D: 0.6497 Loss_G: 5.9927 D(x): 0.7977 D(G(z)): 0.0483 / 0.0026 Elapsed 0.06 s
[0/100][93/472] Loss_D: 0.6727 Loss_G: 8.6965 D(x): 0.8520 D(G(z)): 0.1001 / 0.0002 Elapsed 0.06 s
[0/100][94/472] Loss_D: 0.6081 Loss_G: 9.9745 D(x): 0.7268 D(G(z)): 0.0080 / 0.0000 Elapsed 0.06 s
[0/100][95

[0/100][169/472] Loss_D: 0.5536 Loss_G: 5.1299 D(x): 0.8000 D(G(z)): 0.0133 / 0.0069 Elapsed 0.06 s
[0/100][170/472] Loss_D: 0.5576 Loss_G: 5.0628 D(x): 0.7939 D(G(z)): 0.0164 / 0.0076 Elapsed 0.06 s
[0/100][171/472] Loss_D: 0.5491 Loss_G: 5.2493 D(x): 0.7927 D(G(z)): 0.0137 / 0.0058 Elapsed 0.06 s
[0/100][172/472] Loss_D: 0.5604 Loss_G: 5.0048 D(x): 0.7992 D(G(z)): 0.0202 / 0.0077 Elapsed 0.06 s
[0/100][173/472] Loss_D: 0.5570 Loss_G: 5.2978 D(x): 0.8061 D(G(z)): 0.0172 / 0.0058 Elapsed 0.06 s
[0/100][174/472] Loss_D: 0.5475 Loss_G: 5.5032 D(x): 0.7931 D(G(z)): 0.0142 / 0.0046 Elapsed 0.06 s
[0/100][175/472] Loss_D: 0.5405 Loss_G: 5.8541 D(x): 0.7974 D(G(z)): 0.0106 / 0.0035 Elapsed 0.06 s
[0/100][176/472] Loss_D: 0.5730 Loss_G: 5.2660 D(x): 0.6884 D(G(z)): 0.0108 / 0.0062 Elapsed 0.06 s
[0/100][177/472] Loss_D: 0.5578 Loss_G: 4.6693 D(x): 0.7529 D(G(z)): 0.0205 / 0.0124 Elapsed 0.06 s
[0/100][178/472] Loss_D: 0.5984 Loss_G: 4.5838 D(x): 0.8462 D(G(z)): 0.0451 / 0.0134 Elapsed 0.06 s


[0/100][253/472] Loss_D: 0.5931 Loss_G: 4.6850 D(x): 0.7019 D(G(z)): 0.0222 / 0.0116 Elapsed 0.06 s
[0/100][254/472] Loss_D: 0.6239 Loss_G: 4.6753 D(x): 0.7005 D(G(z)): 0.0125 / 0.0114 Elapsed 0.06 s
[0/100][255/472] Loss_D: 0.6068 Loss_G: 3.9163 D(x): 0.7657 D(G(z)): 0.0282 / 0.0261 Elapsed 0.06 s
[0/100][256/472] Loss_D: 0.6487 Loss_G: 3.4186 D(x): 0.8185 D(G(z)): 0.0647 / 0.0423 Elapsed 0.06 s
[0/100][257/472] Loss_D: 0.6083 Loss_G: 4.0480 D(x): 0.8351 D(G(z)): 0.0568 / 0.0246 Elapsed 0.06 s
[0/100][258/472] Loss_D: 0.6000 Loss_G: 4.5988 D(x): 0.7855 D(G(z)): 0.0363 / 0.0152 Elapsed 0.06 s
[0/100][259/472] Loss_D: 0.6133 Loss_G: 4.4038 D(x): 0.7493 D(G(z)): 0.0442 / 0.0214 Elapsed 0.06 s
[0/100][260/472] Loss_D: 0.6245 Loss_G: 4.2786 D(x): 0.7124 D(G(z)): 0.0444 / 0.0251 Elapsed 0.06 s
[0/100][261/472] Loss_D: 0.6055 Loss_G: 4.0728 D(x): 0.7271 D(G(z)): 0.0504 / 0.0302 Elapsed 0.06 s
[0/100][262/472] Loss_D: 0.6775 Loss_G: 3.5804 D(x): 0.7038 D(G(z)): 0.0553 / 0.0397 Elapsed 0.06 s


...

[99/100][97/472] Loss_D: 0.5720 Loss_G: 5.3112 D(x): 0.6798 D(G(z)): 0.0063 / 0.0069 Elapsed 0.06 s
[99/100][98/472] Loss_D: 0.5721 Loss_G: 4.3416 D(x): 0.6770 D(G(z)): 0.0121 / 0.0183 Elapsed 0.06 s
[99/100][99/472] Loss_D: 0.5436 Loss_G: 3.9416 D(x): 0.8056 D(G(z)): 0.0202 / 0.0261 Elapsed 0.06 s
[99/100][100/472] Loss_D: 0.5595 Loss_G: 3.8287 D(x): 0.8342 D(G(z)): 0.0290 / 0.0281 Elapsed 0.06 s
[99/100][101/472] Loss_D: 0.5985 Loss_G: 4.3778 D(x): 0.9056 D(G(z)): 0.0284 / 0.0171 Elapsed 0.06 s
[99/100][102/472] Loss_D: 0.5579 Loss_G: 4.6311 D(x): 0.8461 D(G(z)): 0.0283 / 0.0131 Elapsed 0.06 s
[99/100][103/472] Loss_D: 0.5927 Loss_G: 4.8512 D(x): 0.6704 D(G(z)): 0.0139 / 0.0106 Elapsed 0.06 s
[99/100][104/472] Loss_D: 0.5323 Loss_G: 5.0588 D(x): 0.7772 D(G(z)): 0.0109 / 0.0088 Elapsed 0.06 s
[99/100][105/472] Loss_D: 0.5455 Loss_G: 4.3856 D(x): 0.7846 D(G(z)): 0.0238 / 0.0184 Elapsed 0.06 s
[99/100][106/472] Loss_D: 0.6058 Loss_G: 4.3282 D(x): 0.6334 D(G(z)): 0.0133 / 0.0185 Elapsed 

[99/100][181/472] Loss_D: 0.5361 Loss_G: 4.7968 D(x): 0.7801 D(G(z)): 0.0099 / 0.0110 Elapsed 0.06 s
[99/100][182/472] Loss_D: 0.5337 Loss_G: 4.2287 D(x): 0.7734 D(G(z)): 0.0164 / 0.0181 Elapsed 0.06 s
[99/100][183/472] Loss_D: 0.6149 Loss_G: 3.4935 D(x): 0.6541 D(G(z)): 0.0247 / 0.0414 Elapsed 0.06 s
[99/100][184/472] Loss_D: 0.5889 Loss_G: 3.1989 D(x): 0.8298 D(G(z)): 0.0582 / 0.0567 Elapsed 0.06 s
[99/100][185/472] Loss_D: 0.6501 Loss_G: 3.5450 D(x): 0.8967 D(G(z)): 0.0725 / 0.0354 Elapsed 0.06 s
[99/100][186/472] Loss_D: 0.5711 Loss_G: 4.3542 D(x): 0.7693 D(G(z)): 0.0290 / 0.0157 Elapsed 0.06 s
[99/100][187/472] Loss_D: 0.5515 Loss_G: 4.5777 D(x): 0.7881 D(G(z)): 0.0222 / 0.0124 Elapsed 0.06 s
[99/100][188/472] Loss_D: 0.5699 Loss_G: 4.8560 D(x): 0.7010 D(G(z)): 0.0131 / 0.0105 Elapsed 0.06 s
[99/100][189/472] Loss_D: 0.5711 Loss_G: 4.4151 D(x): 0.6986 D(G(z)): 0.0142 / 0.0153 Elapsed 0.06 s
[99/100][190/472] Loss_D: 0.5858 Loss_G: 4.1059 D(x): 0.6832 D(G(z)): 0.0142 / 0.0207 Elaps

[99/100][265/472] Loss_D: 0.6353 Loss_G: 4.2996 D(x): 0.5959 D(G(z)): 0.0107 / 0.0185 Elapsed 0.06 s
[99/100][266/472] Loss_D: 0.5770 Loss_G: 3.9160 D(x): 0.8803 D(G(z)): 0.0229 / 0.0250 Elapsed 0.06 s
[99/100][267/472] Loss_D: 0.5689 Loss_G: 3.6757 D(x): 0.8162 D(G(z)): 0.0383 / 0.0322 Elapsed 0.06 s
[99/100][268/472] Loss_D: 0.5500 Loss_G: 4.4805 D(x): 0.8351 D(G(z)): 0.0225 / 0.0151 Elapsed 0.06 s
[99/100][269/472] Loss_D: 0.5929 Loss_G: 4.4699 D(x): 0.8926 D(G(z)): 0.0338 / 0.0146 Elapsed 0.06 s
[99/100][270/472] Loss_D: 0.6006 Loss_G: 4.7566 D(x): 0.6428 D(G(z)): 0.0134 / 0.0110 Elapsed 0.06 s
[99/100][271/472] Loss_D: 0.5732 Loss_G: 4.6655 D(x): 0.6733 D(G(z)): 0.0107 / 0.0137 Elapsed 0.06 s
[99/100][272/472] Loss_D: 0.5597 Loss_G: 4.3368 D(x): 0.8597 D(G(z)): 0.0189 / 0.0174 Elapsed 0.06 s
[99/100][273/472] Loss_D: 0.5665 Loss_G: 4.3772 D(x): 0.8430 D(G(z)): 0.0227 / 0.0164 Elapsed 0.06 s
[99/100][274/472] Loss_D: 0.5742 Loss_G: 5.2683 D(x): 0.8913 D(G(z)): 0.0132 / 0.0072 Elaps

[99/100][349/472] Loss_D: 0.5568 Loss_G: 4.8102 D(x): 0.8579 D(G(z)): 0.0226 / 0.0106 Elapsed 0.06 s
[99/100][350/472] Loss_D: 0.5422 Loss_G: 5.4065 D(x): 0.7318 D(G(z)): 0.0086 / 0.0059 Elapsed 0.06 s
[99/100][351/472] Loss_D: 0.5631 Loss_G: 4.6930 D(x): 0.7070 D(G(z)): 0.0126 / 0.0130 Elapsed 0.06 s
[99/100][352/472] Loss_D: 0.5572 Loss_G: 4.4344 D(x): 0.7156 D(G(z)): 0.0122 / 0.0160 Elapsed 0.06 s
[99/100][353/472] Loss_D: 0.5540 Loss_G: 3.8724 D(x): 0.8143 D(G(z)): 0.0307 / 0.0306 Elapsed 0.06 s
[99/100][354/472] Loss_D: 0.5572 Loss_G: 3.9206 D(x): 0.7956 D(G(z)): 0.0311 / 0.0262 Elapsed 0.06 s
[99/100][355/472] Loss_D: 0.5705 Loss_G: 4.4457 D(x): 0.8723 D(G(z)): 0.0293 / 0.0167 Elapsed 0.06 s
[99/100][356/472] Loss_D: 0.5524 Loss_G: 4.6283 D(x): 0.7535 D(G(z)): 0.0198 / 0.0130 Elapsed 0.06 s
[99/100][357/472] Loss_D: 0.5514 Loss_G: 4.5819 D(x): 0.7478 D(G(z)): 0.0180 / 0.0141 Elapsed 0.06 s
[99/100][358/472] Loss_D: 0.5386 Loss_G: 4.7036 D(x): 0.7779 D(G(z)): 0.0166 / 0.0129 Elaps

[99/100][433/472] Loss_D: 0.6031 Loss_G: 4.3097 D(x): 0.8835 D(G(z)): 0.0520 / 0.0175 Elapsed 0.06 s
[99/100][434/472] Loss_D: 0.5399 Loss_G: 5.7506 D(x): 0.8222 D(G(z)): 0.0133 / 0.0044 Elapsed 0.06 s
[99/100][435/472] Loss_D: 0.6308 Loss_G: 5.8450 D(x): 0.5984 D(G(z)): 0.0048 / 0.0042 Elapsed 0.06 s
[99/100][436/472] Loss_D: 0.7077 Loss_G: 4.5219 D(x): 0.5368 D(G(z)): 0.0059 / 0.0141 Elapsed 0.06 s
[99/100][437/472] Loss_D: 0.5357 Loss_G: 3.9605 D(x): 0.7879 D(G(z)): 0.0126 / 0.0240 Elapsed 0.06 s
[99/100][438/472] Loss_D: 0.5810 Loss_G: 3.2365 D(x): 0.8492 D(G(z)): 0.0461 / 0.0524 Elapsed 0.06 s
[99/100][439/472] Loss_D: 0.6787 Loss_G: 3.7516 D(x): 0.9241 D(G(z)): 0.0711 / 0.0324 Elapsed 0.06 s
[99/100][440/472] Loss_D: 0.5705 Loss_G: 4.5322 D(x): 0.8140 D(G(z)): 0.0413 / 0.0156 Elapsed 0.06 s
[99/100][441/472] Loss_D: 0.6033 Loss_G: 4.6888 D(x): 0.6616 D(G(z)): 0.0189 / 0.0134 Elapsed 0.06 s
[99/100][442/472] Loss_D: 0.5733 Loss_G: 4.3318 D(x): 0.6926 D(G(z)): 0.0152 / 0.0174 Elaps